In [1]:
import geopandas as gpd
import hexseg as HS

#### Load data

In [2]:
# filepaths
base = "https://raw.githubusercontent.com/routineactivity/hexseg/main/data"
districts = f"{base}/bkn_precincts.gpkg"
roads     = f"{base}/bkn_roads_lion.gpkg"
crimes    = f"{base}/bkn_sample_data.gpkg"

gdf_districts = gpd.read_file(districts)
gdf_roads     = gpd.read_file(roads)
gdf_crimes    = gpd.read_file(crimes)

#### Summarise points by segment

In [3]:
roads_with_counts = HS.count_crimes_by_nearest_road(
    crimes_gdf=gdf_crimes,
    roads_gdf=gdf_roads,
    max_dist=75 # set maximum distance from segment to point
    )

#### Build adjacency graph

In [4]:
G = HS.build_adj_graph(roads_with_counts,
                          fid_col=None,
                          crime_count_col='crime_count')

#### Create clusters of segments

Choose minimum and maximum number of segments that clusters should contain. If the use if patrols - think about this in terms of how long/far/distance that would be covered; i.e. 15min Koper might be limited to few rather than many segments; also choose minimum number of crimes that cluster should contain

In [6]:
clusters = HS.segment_clusters(G, min_size=5, max_size=8, min_crimes=100)

#### Add cluster ID and sum of crimes to gdf_roads

In [7]:
gdf_clusters = HS.clusters_to_gdf(clusters, G, roads_with_counts, fid_col='fid', crime_count_col='crime_count')

#### Visualise results

In [9]:
# Visualise the street segment clusters
m = HS.create_folium_map(
      hex_gdf=None,
      hex_query=None,
      seg_gdf=gdf_clusters,
      seg_query="cluster_crime_sum > 200",
      district_gdf=gdf_districts,
      district_query=None) 
      
m

In [12]:
# If you don't want to cluster segments and just see the highest
# Use the roads_with_counts object you created
m = HS.create_folium_map(
      hex_gdf=None,
      hex_query=None,
      seg_gdf=roads_with_counts,
      seg_query="crime_count > 20",
      district_gdf=gdf_districts,
      district_query=None) 
      
m